In [3]:
### Source Tutorial: https://docs.dgl.ai/guide/training-node.html

### Data Set: https://docs.dgl.ai/en/0.6.x/api/python/dgl.data.html#stanford-sentiment-treebank-dataset
# Loading Sentiment Tree Data

from dgl.data import SSTDataset
import matplotlib.pyplot as plt
import networkx as nx

train_data = SSTDataset()
dev_data = SSTDataset(mode='dev')
test_data = SSTDataset(mode='test')
tiny_data = SSTDataset(mode='tiny')

In [2]:
import dgl.nn as dglnn
import torch.nn as nn
import torch.nn.functional as F
class SAGE(nn.Module):
    def __init__(self, in_feats, hid_feats, out_feats):
        super().__init__()
        self.conv1 = dglnn.SAGEConv(
            in_feats=in_feats, out_feats=hid_feats, aggregator_type='mean')
        self.conv2 = dglnn.SAGEConv(
            in_feats=hid_feats, out_feats=out_feats, aggregator_type='mean')

    def forward(self, graph, inputs):
        # inputs are features of nodes
        h = self.conv1(graph, inputs)
        h = F.relu(h)
        h = self.conv2(graph, h)
        return h

In [4]:
def evaluate(model, graph, features, labels, mask):
    model.eval()
    with torch.no_grad():
        logits = model(graph, features)
        logits = logits[mask]
        labels = labels[mask]
        _, indices = torch.max(logits, dim=1)
        correct = torch.sum(indices == labels)
        return correct.item() * 1.0 / len(labels)

In [8]:
import torch
from torch.utils.data import DataLoader
from dgl.nn.pytorch import GraphConv

model = SAGE(1, 256, 1)
opt = torch.optim.SGD(model.parameters(), lr=0.02)

In [10]:
for tree in train_data:
    input_ids = tree.ndata['x']
    labels = tree.ndata['y']
    mask = tree.ndata['mask']
    print(input_ids)
    print(labels)
    print(mask)

tensor([-1, -1,  0,  1, -1, -1,  2, -1,  3, -1, -1, -1, -1,  4, -1,  5, -1,  0,
        -1,  6, -1, -1,  7,  8, -1,  9, -1, 10, 11, 12, 13, -1, 14, -1, 15, -1,
         8, -1, 16, -1,  4, -1, -1, 17, -1, -1, 18, 19, -1, 20, 21, -1, 22, -1,
        -1, -1, -1, -1, 23, 24, 25, -1, 26, -1, 27, 28, 29, -1, 30, 31, 32])
tensor([3, 2, 2, 2, 4, 3, 2, 4, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
        2, 3, 2, 2, 2, 2, 2, 3, 2, 3, 2, 3, 2, 3, 2, 3, 2, 4, 3, 2, 3, 3, 2, 3,
        2, 2, 3, 2, 2, 2, 2, 2, 2, 1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2])
tensor([0, 0, 1, 1, 0, 0, 1, 0, 1, 0, 0, 0, 0, 1, 0, 1, 0, 1, 0, 1, 0, 0, 1, 1,
        0, 1, 0, 1, 1, 1, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 0, 1, 0, 0, 1, 1,
        0, 1, 1, 0, 1, 0, 0, 0, 0, 0, 1, 1, 1, 0, 1, 0, 1, 1, 1, 0, 1, 1, 1])
tensor([-1, -1, -1,  0, -1, 33, -1, 34, 35, -1, -1, 36, 10, -1,  0, -1, -1, 37,
        -1, 36, -1,  0, 38, -1, 12, 39, -1, -1, -1,  2, -1, 40, 41, -1, 14, -1,
        -1, -1, 18, 42, -1, 36, 43, -1, -1, -1,

tensor([4, 2, 4, 4, 3, 2, 3, 4, 2, 4, 4, 2, 1, 3, 2, 3, 2, 3, 2, 3, 3, 2, 3, 2,
        3, 2, 2, 2, 3, 2, 3, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2])
tensor([0, 1, 0, 0, 0, 1, 0, 0, 1, 1, 0, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 1, 0, 1,
        0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 1, 0, 1, 0, 1, 0, 1, 0, 1, 1, 1])
tensor([  -1,  131,   -1,   -1,   -1,    8,   45,   -1,   18,   -1,  278,   -1,
        1110,  308,   32])
tensor([1, 2, 1, 1, 2, 2, 1, 4, 2, 4, 4, 2, 2, 2, 2])
tensor([0, 1, 0, 0, 0, 1, 1, 0, 1, 0, 1, 0, 1, 1, 1])
tensor([  -1,   70,   -1,   -1,  232,   -1,   79,   -1,   -1,   -1,  496,   -1,
        1111,   -1,   18,   -1, 1112, 1113,   13,   -1, 1114,   -1,   -1,   18,
          -1,  589, 1115,   -1,   36, 1116,   -1,   25,   -1,  423,   -1,   -1,
           8,   -1, 1117,   -1,  145,   -1,    4,   -1,    5,   -1,   87,   99,
          32])
tensor([2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 3, 2, 3, 2, 2, 2, 2, 2, 2, 3, 2,
        2, 2, 2, 2, 2, 3, 3, 2, 3, 2, 3, 3, 2, 3, 1, 3, 4, 2, 2, 2

tensor([1, 2, 2, 3, 3, 2, 2, 2, 2, 3, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
        2, 3, 2, 3, 3, 2, 1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
        2, 2, 2, 3, 2, 2, 2, 3, 2, 2, 1, 2, 2, 2, 2, 2, 2, 2, 2])
tensor([0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 1, 1, 1, 0, 1, 0, 1, 1, 1, 0, 0, 1, 1, 0,
        1, 0, 1, 1, 0, 1, 0, 0, 0, 1, 0, 1, 1, 0, 1, 0, 1, 0, 1, 1, 0, 0, 1, 0,
        1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 1, 1])
tensor([  -1,   -1,   -1,   18,   -1,   -1, 1755,  820, 1756,   -1,   -1,   -1,
         159,   -1,   18,  320,   -1, 1757,   -1, 1366, 1758,   -1,   14,   -1,
          -1,   -1,  999,   -1, 1759, 1283,   -1,    4,   -1,   -1,   -1, 1461,
        1760,   13,   -1,   18, 1761,   -1,    4,   -1, 1762,   -1,   92, 1128,
          32])
tensor([2, 3, 3, 2, 3, 3, 2, 4, 2, 2, 2, 2, 2, 2, 2, 2, 2, 3, 2, 3, 3, 1, 2, 2,
        1, 1, 2, 1, 1, 3, 2, 2, 1, 2, 2, 2, 2, 2, 1, 2, 1, 3, 2, 3, 3, 2, 2, 2,
        2])
tensor([0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0, 

tensor([3, 3, 3, 2, 2, 2, 2, 3, 2, 3, 2, 3, 2, 3, 2, 1, 2, 2, 1, 2, 2, 2, 2, 3,
        2, 4, 2, 3, 2, 3, 2, 4, 3, 3, 2, 3, 3, 3, 2, 2, 3, 2, 3, 2, 2, 2, 2, 2,
        2, 2, 2])
tensor([0, 0, 0, 1, 0, 1, 1, 0, 1, 0, 0, 1, 1, 0, 0, 0, 1, 0, 1, 0, 1, 1, 1, 0,
        1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 0, 1, 1, 1, 0, 0, 0, 1, 1, 0, 1, 0,
        1, 1, 1])
tensor([  -1,   -1,   -1,   -1,  483,   -1,    4,   -1,    5, 2303,    2,   -1,
          -1,   -1,    0,   -1, 2304,   -1,  265,  266,   25,   -1,   -1,    0,
          -1, 2305,   -1, 2306, 2307,   -1,   36,   -1, 2308,   -1,   25,   -1,
        2309,   -1,   25,   -1,   -1, 2310,   13, 2311,   32])
tensor([1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 3, 2, 3, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 1, 2, 2, 2, 2, 1, 1, 2, 2, 2])
tensor([0, 0, 0, 0, 1, 0, 1, 0, 1, 1, 1, 0, 0, 0, 1, 0, 1, 0, 1, 1, 1, 0, 0, 1,
        0, 1, 0, 1, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 0, 1, 1, 1, 1])
tensor([  -1,   -1,    0,   -1,   98,

tensor([0, 0, 0, 1, 1, 0, 1, 0, 1, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 0, 1, 0, 0, 1,
        0, 1, 1, 0, 1, 0, 1, 0, 0, 1, 1, 0, 1, 0, 1, 1, 1])
tensor([  -1,   -1,    0, 2726,   -1,   -1,  841,   -1,   86,   -1,  838,   -1,
         166,   -1,   18,   -1, 2727,   -1, 1527,   -1,  494, 2728,   32])
tensor([2, 2, 2, 2, 2, 2, 2, 2, 2, 3, 2, 1, 2, 2, 2, 2, 1, 2, 2, 3, 4, 2, 2])
tensor([0, 0, 1, 1, 0, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 1, 1])
tensor([  -1,   -1,  985,   -1,  225,   -1,   -1,   -1,  482,   -1,   18,  448,
          -1,   36,   -1,   -1,    0,   -1, 2602, 2729,   -1,   36, 2730,   -1,
          44,    5,   -1,   -1,   25,   13,   -1,   -1, 2731,   -1,   -1,    0,
          -1,  671,  285,   -1,   36,   -1,    0,  287,   32])
tensor([4, 2, 4, 1, 2, 1, 1, 2, 2, 2, 2, 3, 1, 2, 1, 1, 2, 1, 0, 3, 2, 2, 2, 2,
        2, 2, 4, 3, 2, 2, 4, 4, 2, 4, 3, 2, 4, 4, 2, 2, 2, 2, 2, 2, 2])
tensor([0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 1, 1, 0, 1, 0, 0, 1, 0, 1, 1, 0, 1, 1, 0,
        1, 1, 

...

tensor([   -1,    -1,    -1,    20,   269,    -1,    36,    -1,    -1, 16255,
           -1,  8715,     8,   314,    -1,    -1,    25,    -1,    -1,   345,
         8539,    25,    -1,    -1,    85,    -1,    86,    -1,    -1,    18,
           -1,   599,   356,    -1,  2620,    -1,   337,    -1,   122,   284,
           32])
tensor([1, 2, 2, 2, 3, 2, 2, 2, 2, 2, 2, 2, 2, 2, 1, 2, 2, 2, 2, 2, 2, 2, 1, 0,
        2, 0, 2, 1, 1, 2, 1, 2, 2, 1, 2, 2, 2, 2, 2, 2, 2])
tensor([0, 0, 0, 1, 1, 0, 1, 0, 0, 1, 0, 1, 1, 1, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0,
        1, 0, 1, 0, 0, 1, 0, 1, 1, 0, 1, 0, 1, 0, 1, 1, 1])
tensor([   -1,   131,    -1,    -1,    -1,     8,   288,    -1,   114,    -1,
           -1,    -1,    -1,    -1,   834,    -1,   352,    -1,  1220,    -1,
          146,   265,    25,    -1,   284,    -1,  2731,    -1,    -1,    18,
        16256,    -1,    36, 12903,    25,    -1, 16257,    -1,  1884,   784,
           32])
tensor([2, 2, 0, 1, 2, 2, 2, 0, 2, 0, 1, 3, 2, 2, 2, 1, 3, 2, 2,

tensor([1, 0, 3, 1, 2, 2, 2, 0, 2, 2, 2, 3, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
        2, 3, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 3, 4, 2, 2, 2, 2,
        2, 4, 2])
tensor([0, 0, 1, 0, 1, 0, 1, 0, 0, 0, 1, 0, 1, 1, 1, 0, 0, 1, 1, 0, 1, 0, 0, 0,
        1, 1, 0, 1, 1, 0, 1, 0, 1, 0, 1, 0, 0, 1, 1, 0, 1, 1, 0, 0, 0, 0, 1, 1,
        1, 1, 1])
tensor([   -1, 10458,    -1,    25,    -1,    -1,    13,    -1,    -1,    -1,
           66,   873,    25,   598,    32])
tensor([3, 2, 2, 2, 3, 3, 2, 3, 3, 3, 2, 4, 2, 2, 2])
tensor([0, 1, 0, 1, 0, 0, 1, 0, 0, 0, 1, 1, 1, 1, 1])
tensor([   -1,   372,    -1,    -1,    -1,   117,    -1,    -1,     0, 10489,
           -1,    36,    -1,  2478, 16358,    -1,   429,    -1,    -1,  6132,
        16359,    -1,   394,    -1,    -1,  1908,   315,    -1,  1909,    -1,
          521,    -1,     4,    -1,  1346,    -1,    -1,    18,    69,    -1,
          155,    -1,    -1,    66,    -1,    22,  1565,  2680,    32])
tensor([0, 2, 2, 0, 1, 2, 0, 2

        0, 1, 0, 0, 1, 1, 0, 1, 0, 0, 1, 1, 0, 1, 0, 1, 1])
tensor([   -1,   131,    -1,    -1,    -1,     8,    -1,    -1,     0,  1477,
           -1,    36,   308,    -1,    14,    -1,    -1,    25,    -1,  5892,
           -1,    -1,   429,    -1,    -1,    -1,    -1,    -1,    -1,    -1,
          524, 12078,    25,    -1,  3244,  3245,    25,    -1,     0,    -1,
         7992,  3608,    13,    -1,    18,    -1,    63,  1128,    25,    -1,
           -1,  1390, 13844,    -1,    -1,  1908,   315,    -1,    17,    -1,
          309,    88,    32])
tensor([4, 2, 4, 3, 2, 2, 2, 2, 2, 3, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 3, 2, 2, 2, 2, 2, 2, 2, 2,
        2, 2, 3, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2])
tensor([0, 1, 0, 0, 0, 1, 0, 0, 1, 1, 0, 1, 1, 0, 1, 0, 0, 1, 0, 1, 0, 0, 1, 0,
        0, 0, 0, 0, 0, 0, 1, 1, 1, 0, 1, 1, 1, 0, 1, 0, 1, 1, 1, 0, 1, 0, 1, 1,
        1, 0, 0, 1, 1, 0, 0, 1, 1, 0, 1, 0, 1, 1, 1])
tensor([   -1,

tensor([3, 3, 1, 3, 2])
tensor([0, 0, 1, 1, 1])
tensor([   -1, 11916,    -1,    70,    -1,  5810,    32])
tensor([2, 1, 2, 2, 3, 3, 2])
tensor([0, 1, 0, 1, 0, 1, 1])
tensor([  -1,   -1,  453, 1504,   -1,   -1,    2,   -1,  743,   -1,    4,   -1,
          -1, 2112,   79,   -1,   -1,   18, 1662,   -1,   36,   -1,  511,   -1,
         117,   -1,  122,   -1,   -1,  248,   -1,   25,   -1,   -1,  601,   13,
        1666,  508,   32])
tensor([4, 2, 2, 2, 4, 4, 2, 4, 2, 4, 2, 4, 3, 3, 2, 4, 2, 2, 2, 3, 2, 3, 3, 3,
        2, 3, 2, 4, 3, 2, 4, 2, 4, 3, 4, 2, 2, 3, 2])
tensor([0, 0, 1, 1, 0, 0, 1, 0, 1, 0, 1, 0, 0, 1, 1, 0, 0, 1, 1, 0, 1, 0, 1, 0,
        1, 0, 1, 0, 0, 1, 0, 1, 0, 0, 1, 1, 1, 1, 1])
tensor([  -1,  599,   -1,   -1,    4, 2234,   32])
tensor([3, 2, 2, 2, 2, 1, 2])
tensor([0, 1, 0, 0, 1, 1, 1])
tensor([   -1,    18,    -1, 16523,    -1,  4329,    32])
tensor([4, 2, 4, 3, 3, 4, 2])
tensor([0, 1, 0, 1, 0, 1, 1])
tensor([ -1,  -1,  18, 145,  -1, 169,  32])
tensor([3, 3, 2, 4, 2, 2, 

tensor([0, 0, 1, 1, 1])
tensor([  -1, 1217,   -1, 6159,   32])
tensor([1, 2, 1, 1, 2])
tensor([0, 1, 0, 1, 1])
tensor([  -1,   -1, 4907,  873,   32])
tensor([2, 3, 2, 4, 2])
tensor([0, 0, 1, 1, 1])
tensor([  -1, 2420,   32])
tensor([0, 0, 2])
tensor([0, 1, 1])
tensor([   -1,    -1, 16568,    -1,   312, 16569,    32])
tensor([0, 1, 1, 1, 2, 0, 2])
tensor([0, 0, 1, 0, 1, 1, 1])
tensor([  -1,   -1,   -1, 4325,   13, 5873,   32])
tensor([1, 0, 2, 2, 2, 1, 2])
tensor([0, 0, 0, 1, 1, 1, 1])
tensor([   -1, 16039,    32])
tensor([0, 0, 2])
tensor([0, 1, 1])
tensor([  -1,   -1,  109, 1826,   -1, 9708,   32])
tensor([1, 2, 2, 2, 2, 2, 2])
tensor([0, 0, 1, 1, 0, 1, 1])
tensor([   -1, 15860,    32])
tensor([1, 1, 2])
tensor([0, 1, 1])
tensor([   -1,    -1, 10965,    -1, 16570,  5825,    32])
tensor([1, 1, 1, 2, 2, 2, 2])
tensor([0, 0, 1, 0, 1, 1, 1])
tensor([   -1,    -1, 14737, 13983,    32])
tensor([1, 0, 1, 1, 2])
tensor([0, 0, 1, 1, 1])
tensor([   -1, 16435,    -1,    25,    -1,    -1, 15204, 

In [ ]:
for epoch in range(10):
#     model.train()
#     # forward propagation by using all nodes
#     logits = model(graph, node_features)
#     # compute loss
#     loss = F.cross_entropy(logits[train_mask], node_labels[train_mask])
#     # compute validation accuracy
#     acc = evaluate(model, graph, node_features, node_labels, valid_mask)
#     # backward propagation
#     opt.zero_grad()
#     loss.backward()
#     opt.step()
#     print(loss.item())
    
    model.train()

    epoch_losses = [] # MSE average list
    epoch_r_losses = [] # RMSE average list
    for epoch in range(curr_epoch_range):
        epoch_loss = 0
        epoch_r_loss = 0
        for tree in train_data:
            input_ids = tree.ndata['x']
            labels = tree.ndata['y']
            mask = tree.ndata['mask']
            prediction = model(tree, labels)
            print(prediction)
            loss = loss_func(prediction, label)
            optimizer.zero_grad()
            loss.backward()
            optimizer.step()
            # Mean Relative Error
            MRE_loss = np.average(np.abs(np.array(prediction.detach().numpy()) - np.array(label.detach().numpy()))/np.abs(np.array(label.detach().numpy())))
            epoch_loss += loss.detach().item()
            if np.isinf(MRE_loss):
                print(bg)
                print(label)
            print(MRE_loss)
            epoch_r_loss += MRE_loss
        epoch_loss /= (iter + 1)
        epoch_r_loss /= (iter + 1)

        epoch_losses.append(epoch_loss)
        epoch_r_losses.append(epoch_r_loss)
    return epoch_losses, epoch_r_losses